# Diskrétní logaritmus

Pro práci s diskrétním logaritmem využijeme Computer Algebra System (CAS) SageMath. Pomocí třidy `Integers` můžeme vytvořit těleso modulo $n$.

In [ ]:
R = Integers(10031)

display(R(4321))

In [ ]:
num = R(4321)^1234 # umocňování je prováděno modulo 10031!

display(num)

## Graf exponenciály $2^x$

In [ ]:
my_exp(x) = 2^x

p = plot(my_exp, (1, 7), thickness=2, legend_label='$2^x$')
p.show(legend_font_size=18)

## Graf umocňování modulo 31

Zkusme si nyní vykreslit graf umocňování trojky modulo 31.

In [ ]:
R7 = Integers(31)
# trojka = R7(3)

nums = []

for exponent in range(1, 30):
    nums.append((exponent, R7(3)^exponent))

display(nums[:5])

In [ ]:
p = list_plot(nums, size=100, gridlines=True, legend_label='$3^x$ mod $31$')
p.show(legend_font_size=15)

## Diskrétní logaritmus v Sagi

Pomocí metody `log` můžeme vypočítat diskrétní logaritmus. Modulus i výsledek známe, musíme jenom metodě předat základ mocniny.

In [ ]:
R = Integers(11)
num = R(5)^3 # umocňování je prováděno modulo 11!

print(f"vysledek 5^3 mod 11: {num}")

In [ ]:
print(f"na kolikatou musim umocnit 5, abych ziskal 4? {num.log(5)}")

Nyní si zkusíme změřit, jak dlouho trvá spočítat diskrétní logaritmus pro nějaké náhodné hodnoty. Funkce `random_nbit_power` nám vygeneruje náhodný problém diskrétního logaritmu. Vstup `bits` nám říká, kolik bitů bude mít prvočíslo $p$, modulo které počítáme.

In [ ]:
from sympy import randprime

def random_nbit_power(bits):
    order = randprime(2^(bits-1), 2^bits - 1)

    R = Integers(order)

    base = R.multiplicative_generator()

    exp = 0
    
    while exp < int(order * (3/4)):
        exp = R.random_element()

    num = base^exp

    return (num, base)

In [ ]:
result = random_nbit_power(20)

print(result)

%timeit result[0].log(result[1])

In [ ]:
result2 = random_nbit_power(50)

print(result2)

%timeit result2[0].log(result2[1])

## Graf složitosti výpočtu diskrétního logaritmu

Zkusíme si změřit trvání diskrétního logaritmu pro různě velká čísla. Postupně půjdeme od $40$ bitových až po $110$ bitové čísla, pro každé z nich vyřešíme diskrétní logaritmus a zaznamenáme čas.

In [ ]:
from numpy import mean

timings = []

for n in range(40, 111, 10):
    problem = random_nbit_power(n)

    timing = %timeit -n1 -o problem[0].log(problem[1])
    timings.append((n, mean(timing.timings) * 1000))

print(timings)

### Graf měření

Výsledek můžeme zakreslit do grafu, kde na ose $x$ bude počet bitů a na ose $y$ bude doba výpočtu diskrétního logaritmu.

In [ ]:
plt = points(timings, size=100)
plt.axes_labels(["počet bitů", "doba výpočtu v ms"])
plt.show(frame=True)

Zkusíme najít křivku, která popisuje naše měření.

In [ ]:
# hledame krivku ve tvaru co je nize popsan

var('a, b, x')
model(x) = a * exp((b + (8/3)^(2/3)) * (log(x))^(1/3) * log(log(x))^(2/3))

# tohle dela nejakou optimalizacni magii
params = find_fit(timings, model)
params

### Graf křivky popisující růst

In [ ]:
# magie se sagem

a = params[0].rhs()
b = params[1].rhs()
fn(x) = a * exp((b + (8/3)^(2/3)) * (log(x))^(1/3) * log(log(x))^(2/3))

plt2 = plt + plot(fn, (x, 0, 130))
plt2.show(frame=True)